Import the Python modules

In [1]:
# %reset -f
import os, sys
import random
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import healpy as hp
import rubin_sim
import rubin_sim.maf as maf
import rubin_sim.utils as rsUtils
from rubin_sim.data import get_baseline
from rubin_sim.maf.utils import m52snr
#version 2
from pyLIMA.simulations import simulator
from pyLIMA import event
from pyLIMA import telescopes

from scipy.interpolate import interp1d

from rubin_sim.phot_utils import signaltonoise
from rubin_sim.phot_utils import PhotometricParameters
from rubin_sim.phot_utils import bandpass_dict

import matplotlib.pyplot as plt
import numpy as np


In [2]:
def set_photometric_parameters(exptime, nexp, readnoise=None):
    # readnoise = None will use the default (8.8 e/pixel). Readnoise should be in electrons/pixel.
    photParams = PhotometricParameters(exptime=exptime, nexp=nexp, readnoise=readnoise)
    return photParams

photParams = set_photometric_parameters(30,1)
LSST_BandPass = bandpass_dict.BandpassDict.load_total_bandpasses_from_files()#bandpass_dict.load_total_bandpasses_from_files()
default5sigma = {'u':23.78, 'g':24.81, 'r':24.35 , 'i':23.92, 'z': 23.34 , 'y':22.45}
# for f in ()
f = 'u'
magerr, gamma = signaltonoise.calc_mag_error_m5(17., LSST_BandPass[f], default5sigma[f], photParams)

print("mag_err: {0} gamma {1}".format(magerr, gamma))

mag_err: 0.00541754476933731 gamma 0.038169261213215004


In [3]:
import astropy.units as u
from astropy.coordinates import SkyCoord
gc = SkyCoord(l=0.5*u.degree, b=-1.25*u.degree, frame='galactic')
gc.icrs.dec.value
Ra = gc.icrs.ra.value
Dec = gc.icrs.dec.value
print(Ra,Dec)

267.92497054815516 -29.152232510353276


# Extract the timestamps from OpSim 


In [4]:
# baseline_file = get_baseline()
# print(baseline_file)

In [5]:
baseline_file = get_baseline()
name = os.path.basename(baseline_file).replace('.db','')

outDir = 'temp'
resultsDb = maf.db.ResultsDb()

print(baseline_file)
print(name)

/home/anibal-art/rubin_sim_data/sim_baseline/baseline_v2.0_10yrs.db
baseline_v2.0_10yrs


In [6]:
bundleList = []
ra = [Ra]
dec = [Dec]
metric = maf.metrics.PassMetric(cols=['filter', 'observationStartMJD', 'fiveSigmaDepth'])
sql = ''
slicer = maf.slicers.UserPointsSlicer(ra=ra, dec=dec)
print(slicer)
bundleList.append(maf.MetricBundle(metric, slicer, sql))

In [7]:
example1_bg = maf.MetricBundleGroup(bundleList, baseline_file, out_dir=outDir)
example1_bg.run_all()
dataSlice = bundleList[0].metric_values[0]

In [8]:
filters = ['u','g','r','i','z','y']
for fil in filters:
    int_array = np.empty((0,3), int)
    for i in range(len(dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == fil)])):
        m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == fil)][i]
        mjd = dataSlice['observationStartMJD'][np.where(dataSlice['filter'] == fil)][i]
        mags = np.random.uniform(15.,m5-0.15)
        # mags = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == fil)]
        magerr = signaltonoise.calc_mag_error_m5(mags,  LSST_BandPass[fil],m5 , photParams)
        int_array = np.append(int_array, [[mjd,mags,magerr[0]]],axis=0)
    np.savetxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_'+fil+'.txt', int_array)

magu = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_u.txt')
magg = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_g.txt')
magr = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_r.txt')
magi = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_i.txt')
magz = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_z.txt')
magy = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/simulation/lc_timestamps_lsst/lightcurve_y.txt')

magu[:,0] = magu[:,0]+2400000.5
magg[:,0] = magg[:,0]+2400000.5
magr[:,0] = magr[:,0]+2400000.5
magi[:,0] = magi[:,0]+2400000.5
magz[:,0] = magz[:,0]+2400000.5
magy[:,0] = magy[:,0]+2400000.5

In [9]:
# me pregunto cual sera el primer dia de observacion
min(list(dataSlice['observationStartMJD']))

60413.26382860778

## Define the microlensing parameters

For binary lens the parameters are:\
$t_0$: time of maximum magnification\
$u_0$: impact parameter\
$t_E$: Einstein time\
log(s): The separation (s) between the two lensing objects, which determines the distance between the two lensing masses.\
q: The mass ratio (q) between the two lensing objects, which determines the relative strength of the two lensing masses.\
$\alpha$: The angle (alpha) between the source-lens and source-observer lines of sight, which determines the orientation of the lensing system.\
$\pi_{EE}$, $\pi_{EN}$: normal distributions.


The distributions used are:

For tE a lognormal distribution with mean 3.1 and sigma = 1. That mimics the observed distribution toward the Galactic Bulge (Mroz et. al 2017)

t0 is obtain from a uniform distribution that expand on a interval that allows Roman and Rubin see the same event.


uo from a uniform distribution in [0,1]



# Read data from TRILEGAL simulation output

 http://stev.oapd.inaf.it/cgi-bin/trilegal
 
 ra = 270
 
 dec = -30
 
 filtros: LSST + WFIRST
 
 The zero point has been updated with the info here https://smtn-002.lsst.io/#useful-github-repositories
 
 
The noise saturation limit 14.8 mag is obtained from Penny. et al https://iopscience.iop.org/article/10.3847/1538-4365/aafb69/pdf

In [10]:
data = pd.read_csv('/home/anibal-art/ROMAN-RUBIN/output445007434654.dat', sep="\s+", decimal ='.', header = [0])

data = data.drop([len(data['u'])-1])
# data = data[data['W149']>14.8]
# data = data[data['W149']<29]
data = data[data['i']<28]
data['W149'] = data['W149']+1.2258 #transform Vega magnitudes into AB
display(data)



#Gc  logAge  [M/H]    m_ini   logL  logTe   logg  m-M0     Av  \
0           1    6.65  -0.41  0.20008 -2.167  3.564  5.109  12.9  0.026   
1           1    6.65  -0.41  0.03868 -2.491  3.434  4.197  13.5  0.029   
2           1    6.65  -0.41  0.24626 -1.992  3.575  5.068  14.3  0.032   
3           1    6.65  -0.41  0.06566 -2.198  3.466  4.261  14.4  0.032   
4           1    6.65  -0.41  0.10981 -1.835  3.514  4.316  15.0  0.032   
...       ...     ...    ...      ...    ...    ...    ...   ...    ...   
19769616    1    9.41   0.01  0.11113 -2.923  3.466  5.216  13.1  0.027   
19769617    1    9.41   0.01  0.55982 -1.228  3.610  4.800  13.1  0.027   
19769618    1    9.41   0.01  1.05689  0.065  3.770  4.423  13.1  0.027   
19769619    1    9.41   0.01  0.24844 -2.048  3.551  5.030  13.1  0.027   
19769620    1    9.41   0.01  0.11929 -2.851  3.472  5.202  13.1  0.027   

          m2/m1  ...       z       Y    R062    Z087    Y106    J129    H158  \
0          0.00  ...  22.687  22.509  23.600  22.202  21.746  21.293  20.891   
1          0.00  ...  24.371  23.905  26.615  23.870  22.977  22.471  22.111   
2          0.00  ...  23.641  23.470  24.477  23.156  22.718  22.277  21.874   
3          0.00  ...  24.395  24.072  26.276  23.912  23.192  22.686  22.287   
4          0.80  ...  23.416  23.174  24.797  22.935  22.358  21.865  21.466   
...         ...  ...     ...     ...     ...     ...     ...     ...     ...   
19769616   0.94  ...  24.277  23.904  26.278  23.790  23.013  22.519  22.143   
19769617   0.97  ...  19.861  19.712  20.522  19.373  18.975  18.517  18.039   
19769618   0.00  ...  17.496  17.489  17.499  17.005  16.852  16.595  16.368   
19769619   0.84  ...  22.013  21.802  23.187  21.533  21.022  20.554  20.157   
19769620   0.00  ...  24.712  24.368  26.584  24.228  23.498  23.007  22.632   

            F184     W149   Mact  
0         20.734  22.4888  0.200  
1         21.980  23.7048  0.039  
2         21.728  23.4708  0.246  
3         22.183  23.9078  0.066  
4         21.320  23.0758  0.110  
...          ...      ...    ...  
19769616  22.042  23.7488  0.111  
19769617  17.875  19.6738  0.560  
19769618  16.307  17.8248  1.057  
19769619  19.987  21.7538  0.248  
19769620  22.520  24.2348  0.119  

[19769621 rows x 25 columns]

In [11]:
# function to convert flux into mag

def mag(zp, Flux):
    return zp-2.5*np.log10(abs(Flux))

def magerr(Flux,Flux_err):
    return np.abs(2.5*Flux_err/(np.log(10)*Flux))

def filter_band(mjd,mag,magerr,m5,fil):
    
    mag_sat = {'w':14.8, 'u':14.7, 'g': 15.7, 'r': 15.8, 'i': 15.8, 'z': 15.3, 'y': 13.9}
    MJD = []
    MAG = []
    MAGERR = []
    M5 = []
    for i in range(len(mjd)):
        if mag[i]+ magerr[i]>mag_sat[fil] and mag[i] + magerr[i]<m5[i]:
            MJD.append(mjd[i])
            MAGERR.append(magerr[i])
            MAG.append(mag[i])
            M5.append(m5[i])
            
    if not len(MAG)>10:
        MJD, MAG, MAGERR,M5 = [],[],[],[]
        
#     if not len(MJD)==0:
#         npts = []
#         for i in range(len(MJD)):
#             if t0-tE<MJD[i]<t0+tE:
#                 npts.append(1)
#         if not sum(npts)>=5:
#             MJD, MAG, MAGERR, M5 = [],[],[],[]
            
    return MJD, MAG, MAGERR, M5
        
def filter5points(t0,tE,bands):
    fivepts = False
    for b in bands:
        if not len(b)==0:
            MJD = b[:,1]
#             print(MJD)
            npts = []
            for i in range(len(MJD)):
                if t0-tE<float(MJD[i])<t0+tE:
                    npts.append(1)  
            if sum(npts)>=5:
                fivepts = True
                break
    return fivepts

    
def save(path_to_save,i,magstar,params,bandF146,bandU,bandG,bandR,bandI,bandZ,bandY):
    print('saving...')
    t0 = params[0]
    u0 = params[1]
    tE = params[2]
    s = params[3]
    q = params[4]
    alpha = params[5]
    piEN = params[6]
    piEE = params[7]
    
    with open(path_to_save+'Event_'+str(i)+'.txt', 'w') as w:
        w.write('TRILEGAL simulation: output445007434654 \n')
        w.write('Source:'+ str(i)+'\n')
        w.write('w:'+str(magstar[0])+'\n')
        w.write('u:'+str(magstar[1])+'\n')
        w.write('g:'+str(magstar[2])+'\n')
        w.write('r:'+str(magstar[3])+'\n')
        w.write('i:'+str(magstar[4])+'\n')
        w.write('z:'+str(magstar[5])+'\n')
        w.write('y:'+str(magstar[6])+'\n')
        w.write('Microlensing event parameters:\n')
        w.write('t0:'+str(t0)+'\n')
        w.write('u0:'+str(u0)+'\n')
        w.write('tE:'+str(tE)+'\n')
        w.write('s:'+str(s)+'\n')
        w.write('q:'+str(q)+'\n')
        w.write('alpha:'+str(alpha)+'\n')
        w.write('piEN:'+str(piEN)+'\n')
        w.write('piEE:'+str(piEE)+'\n')
        w.write('\n')
        w.write('band,mjd,mag,magerr,m5\n')
        np.savetxt(w,bandF146, delimiter=', ',fmt="%s")
        np.savetxt(w,bandU, delimiter=', ',fmt="%s")
        np.savetxt(w,bandG, delimiter=', ',fmt="%s")
        np.savetxt(w,bandR, delimiter=', ',fmt="%s")
        np.savetxt(w,bandI, delimiter=', ',fmt="%s")
        np.savetxt(w,bandZ, delimiter=', ',fmt="%s")
        np.savetxt(w,bandY, delimiter=', ',fmt="%s")
    print('finish!')

# Compute the fluxes and plot the light curves

In [12]:
from pyLIMA.toolbox import time_series
RA = 267.92497054815516 
DEC = -29.152232510353276

tlsst = min(list(dataSlice['observationStartMJD']))+2400000.5
tstart_Roman = tlsst + 3*365 #Roman is expected to be launch in may 2027


my_own_creation = event.Event(ra=RA, dec=DEC)
my_own_creation.name = 'An event observed by Roman'


Roman1 = simulator.simulate_a_telescope(name='W149', time_start=tstart_Roman,time_end=tstart_Roman+72,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)
Roman2 = simulator.simulate_a_telescope(name='W149',time_start =tstart_Roman+107+72,time_end=tstart_Roman+107+72*2,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)
Roman3 = simulator.simulate_a_telescope(name='W149',time_start=tstart_Roman+107+72*2+113, time_end=tstart_Roman+107+72*3+113,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)
Roman4 = simulator.simulate_a_telescope(name='W149',time_start=tstart_Roman+107+72*3+113+838.36, time_end=tstart_Roman+107+72*4+113+838.36,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)
Roman5 = simulator.simulate_a_telescope(name='W149',time_start=tstart_Roman+107+72*4+113*2+838.36,time_end=tstart_Roman+107+72*5+113*2+838.36,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)
Roman6 = simulator.simulate_a_telescope(name='W149',time_start=tstart_Roman+107+72*4+113*2+838.36+72+107, time_end=tstart_Roman+107+72*4+113*2+838.36+72+107+72,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)
Roman_tot = simulator.simulate_a_telescope(name='W149',time_start=tstart_Roman+107+72*5+113*2+838.36+107, time_end=tstart_Roman+107+72*5+113*2+838.36+107+72,sampling=0.25, 
                                        location='Space',camera_filter='W149',uniform_sampling=True, astrometry=False)

new_array = np.r_[Roman1.lightcurve_flux,Roman2.lightcurve_flux,Roman3.lightcurve_flux,Roman4.lightcurve_flux,Roman5.lightcurve_flux,Roman6.lightcurve_flux]
new_table = time_series.construct_time_series(new_array,['time','flux','err_flux'],['JD','W/m^2','W/m^2'])

Roman_tot.lightcurve_flux = new_table

ephemerides = np.loadtxt('/home/anibal-art/ROMAN-RUBIN/ephemeris/james_webb.txt')
ephemerides[:,0] = ephemerides[:,0]- 2400000.5+2400000.5
ephemerides[:,3] *=  60*300000/150000000
deltaT = tlsst-ephemerides[:,0][0]
ephemerides[:,0] = ephemerides[:,0]+deltaT

Roman_tot.location = 'Space'
Roman_tot.spacecraft_name = 'WFIRST_W149'
Roman_tot.spacecraft_positions = {'astrometry':[],'photometry': ephemerides}

my_own_creation.telescopes.append(Roman_tot)

LSST_u = telescopes.Telescope(name='u', camera_filter='u', location='Earth', light_curve=magu.astype(float),
                              light_curve_names = ['time','mag','err_mag'], light_curve_units = ['JD','mag','mag'])

LSST_g = telescopes.Telescope(name='g', camera_filter='g', location='Earth', light_curve=magg.astype(float),
                              light_curve_names = ['time','mag','err_mag'], light_curve_units = ['JD','mag','mag'])


LSST_r = telescopes.Telescope(name='r', camera_filter='r', location='Earth', light_curve=magr.astype(float),
                              light_curve_names = ['time','mag','err_mag'],light_curve_units = ['JD','mag','mag'])


LSST_i = telescopes.Telescope(name='i', camera_filter='i', location='Earth', light_curve=magi.astype(float),
                              light_curve_names = ['time','mag','err_mag'],light_curve_units = ['JD','mag','mag'])


LSST_z = telescopes.Telescope(name='z', camera_filter='z', location='Earth', light_curve=magz.astype(float),
                              light_curve_names = ['time','mag','err_mag'], light_curve_units = ['JD','mag','mag'])

LSST_y = telescopes.Telescope(name='y', camera_filter='y', location='Earth', light_curve=magy.astype(float),
                              light_curve_names = ['time','mag','err_mag'], light_curve_units = ['JD','mag','mag'])


my_own_creation.telescopes.append(LSST_u)
my_own_creation.telescopes.append(LSST_g)
my_own_creation.telescopes.append(LSST_r)
my_own_creation.telescopes.append(LSST_i)
my_own_creation.telescopes.append(LSST_z)
my_own_creation.telescopes.append(LSST_y)


In [13]:
from pyLIMA.models import PSBL_model
from IPython.core.debugger import Pdb 
from astropy.table import Table

import matplotlib.pyplot as plt
path_to_save='/home/anibal-art/ROMAN-RUBIN/simulation/lightcurves/filtered_curves/'

photParams_u = set_photometric_parameters(30,1)
photParams_grizy = set_photometric_parameters(15,2)
photParams = [photParams_u,photParams_grizy]

# tinicial = time.time()
telescope_bands = ['F146', 'u', 'g', 'r','i','z','y']
cero_p = [27.615, 27.03, 28.38, 28.16, 27.85,  27.46, 26.68]
mag_sat = [14.8, 14.7, 15.7, 15.8, 15.8, 15.3, 13.9]
filterset = ['w146','u','g','r','i','z','y']



for i in range(0,10000):
    print(i)
    # random.seed(i)
    np.random.seed(i)
    tE = np.random.lognormal(3.1, 1)
    t0 = np.random.uniform(tstart_Roman,tstart_Roman+5*365) # from 100 day before Roman is launched to one year later
    u0 = np.random.uniform(1e-6,1)
    q = np.random.uniform(0.00009,1)
    alpha = np.random.uniform(0,180)
    s = np.random.uniform(1e-3, 5)
    piEN = np.random.normal(0.164267,0.749409)
    piEE = np.random.normal(0.044996,0.259390)
    
    my_own_parameters = [t0, u0, tE, s, q, alpha, piEN, piEE]
    
    my_own_model = PSBL_model.PSBLmodel(my_own_creation ,parallax=['Full', t0])
    pyLIMA_parameters_1 = my_own_model.compute_pyLIMA_parameters(my_own_parameters)
    simulator.simulate_lightcurve_flux(my_own_model, pyLIMA_parameters_1)
    
    magstar = [data['W149'].values[i],data['u'].values[i],data['g'].values[i],
               data['r'].values[i],data['i'].values[i],data['z'].values[i],data['Y'].values[i]]

    fs = []
    my_own_flux_parameters = []
    np.random.seed(i)
    for m in range(len(magstar)):
        ZP = cero_p[m] 
        mag_baseline = magstar[m]
        flux_baseline = 10**((ZP-mag_baseline)/2.5)
        g = np.random.uniform(0,1)
        f_source = flux_baseline/(1+g)
        fs.append(f_source)
        my_own_flux_parameters.append(f_source)
        my_own_flux_parameters.append(g)
    my_own_parameters += my_own_flux_parameters
    pyLIMA_parameters = my_own_model.compute_pyLIMA_parameters(my_own_parameters)
    simulator.simulate_lightcurve_flux(my_own_model, pyLIMA_parameters)

    for k in range(1,len(my_own_creation.telescopes)):
        model_flux = my_own_model.compute_the_microlensing_model(my_own_creation.telescopes[k],
                                                                 pyLIMA_parameters)['photometry']
        my_own_creation.telescopes[k].lightcurve_flux['flux'] = model_flux
        
    j=0
    for telo in my_own_creation.telescopes:
        if j==0:
            x = telo.lightcurve_magnitude['time'].value
            y = telo.lightcurve_magnitude['mag'].value
            z = telo.lightcurve_magnitude['err_mag'].value       
            m5 = np.ones(len(x))*27.6
            X,Y,Z,sigma_5 = filter_band(x,y-27.4+cero_p[0],z,m5,'w')
#             print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandF146 = np.c_[['w']*len(X),X,Y,Z,sigma_5]
        if j==1:
            X = telo.lightcurve_flux['time'].value
            ym = mag(cero_p[j],telo.lightcurve_flux['flux'].value)
            z = []
            y = []
            x = []
            M5 = []
            for k in range(len(ym)):
                m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == filters[j-1])][k]
                magerr = signaltonoise.calc_mag_error_m5(ym[k],  LSST_BandPass[filters[j-1]], m5 , photParams[0])[0]
                z.append(magerr)
                y.append(np.random.normal(ym[k],magerr))
                x.append(X[k])
                M5.append(m5)
            X,Y,Z,sigma_5 = filter_band(x,y,z,M5,'u')
#             print(X,Y,Z,sigma_5)
#print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandU = np.c_[[filterset[j]]*len(X),X,Y,Z,sigma_5]

#             bandU = np.c_[['u']*len(x),x,y,z,M5]
#             print('HERE IT IS', bandU)
        if j==2:
            X =  telo.lightcurve_flux['time'].value
            ym = mag(cero_p[j],telo.lightcurve_flux['flux'].value)
            z = []
            y = []
            x = []
            M5 = []
            for k in range(len(ym)):
                m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == filters[j-1])][k]
                magerr = signaltonoise.calc_mag_error_m5(ym[k],  LSST_BandPass[filters[j-1]], m5 , photParams[1])[0]
                z.append(magerr)
                y.append(np.random.normal(ym[k],magerr))
                x.append(X[k])
                M5.append(m5)

            X,Y,Z,sigma_5 = filter_band(x,y,z,M5,'g')
#             print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandG = np.c_[[filterset[j]]*len(X),X,Y,Z,sigma_5]
        if j==3:
            X =  telo.lightcurve_flux['time'].value
            ym = mag(cero_p[j],telo.lightcurve_flux['flux'].value)
            z = []
            y = []
            x = []
            M5 = []
            for k in range(len(ym)):
                m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == filters[j-1])][k]
                magerr = signaltonoise.calc_mag_error_m5(ym[k],  LSST_BandPass[filters[j-1]], m5 , photParams[1])[0]
                z.append(magerr)
                y.append(np.random.normal(ym[k],magerr))
                x.append(X[k])
                M5.append(m5)
            X,Y,Z,sigma_5 = filter_band(x,y,z,M5,'r')
#             print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandR = np.c_[[filterset[j]]*len(X),X,Y,Z,sigma_5]
        if j==4:
            X =  telo.lightcurve_flux['time'].value
            ym = mag(cero_p[j],telo.lightcurve_flux['flux'].value)
            z = []
            y = []
            x = []
            M5 = []
            for k in range(len(ym)):
                m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == filters[j-1])][k]
                magerr = signaltonoise.calc_mag_error_m5(ym[k],  LSST_BandPass[filters[j-1]], m5 , photParams[1])[0]
                z.append(magerr)
                y.append(np.random.normal(ym[k],magerr))
                x.append(X[k])
                M5.append(m5)
            X,Y,Z,sigma_5 = filter_band(x,y,z,M5,'i')
#             print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandI = np.c_[[filterset[j]]*len(X),X,Y,Z,sigma_5]
        if j==5:
            X =  telo.lightcurve_flux['time'].value
            ym = mag(cero_p[j],telo.lightcurve_flux['flux'].value)
            z = []
            y = []
            x = []
            M5 = []
            for k in range(len(ym)):
                m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == filters[j-1])][k]
                magerr = signaltonoise.calc_mag_error_m5(ym[k],  LSST_BandPass[filters[j-1]], m5 , photParams[1])[0]
                z.append(magerr)
                y.append(np.random.normal(ym[k],magerr))
                x.append(X[k])
                M5.append(m5)
            X,Y,Z,sigma_5 = filter_band(x,y,z,M5,'z')
#             print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandZ = np.c_[[filterset[j]]*len(X),X,Y,Z,sigma_5]
        if j==6:
            X =  telo.lightcurve_flux['time'].value
            ym = mag(cero_p[j],telo.lightcurve_flux['flux'].value)
            z = []
            y = []
            x = []
            M5 = []
            for k in range(len(ym)):
                m5 = dataSlice['fiveSigmaDepth'][np.where(dataSlice['filter'] == filters[j-1])][k]
                magerr = signaltonoise.calc_mag_error_m5(ym[k],  LSST_BandPass[filters[j-1]], m5 , photParams[1])[0]
                z.append(magerr)
                y.append(np.random.normal(ym[k],magerr))
                x.append(X[k])
                M5.append(m5)
            X,Y,Z,sigma_5 = filter_band(x,y,z,M5,'y')
#             print(len(X))
#             plt.errorbar(X,Y,Z,linestyle=' ',marker='o')
            bandY = np.c_[[filterset[j]]*len(X),X,Y,Z,sigma_5]
        j += 1
#     plt.show()
    bands=[bandF146,bandU,bandG,bandR,bandI,bandZ,bandY]
    if filter5points(t0,tE,bands):
        if not len(bandF146)==0:
            if not len(bandU)+len(bandG)+len(bandR)+len(bandI)+len(bandZ)+len(bandY)==0:
                save(path_to_save,i,magstar,my_own_parameters,bandF146,bandU,bandG,bandR,bandI,bandZ,bandY)
    

0


/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utctai" yielded 41472 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),
/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utctai" yielded 1 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),
/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utctai" yielded 19 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),


Parallax(Full) estimated for the telescope W149: SUCCESS


/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utcut1" yielded 19 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),
/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utctai" yielded 136 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),
/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utcut1" yielded 136 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),
/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utctai" yielded 137 of "dubious year (Note 3)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),
/home/anibal-art/.local/lib/python3.9/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "utcut1" yielded 137 of "dubious

Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
saving...
finish!
1
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
2
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS


...

9893
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9894
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9895
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Para

9915
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9916
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9917
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Para

9937
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9938
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9939
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Para

9959
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
saving...
finish!
9960
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
saving...
finish!
9961
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimat

9981
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9982
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Parallax(Full) estimated for the telescope i: SUCCESS
Parallax(Full) estimated for the telescope z: SUCCESS
Parallax(Full) estimated for the telescope y: SUCCESS
9983
Parallax(Full) estimated for the telescope W149: SUCCESS
Parallax(Full) estimated for the telescope u: SUCCESS
Parallax(Full) estimated for the telescope g: SUCCESS
Parallax(Full) estimated for the telescope r: SUCCESS
Para